# 1. Import libraries and data
# 2. General Data checking
# 3. Subsetting/cleaning
# 4. Aggregating averages
# 5. Plot Choropleths
# 6. Discuss results

# ------------------------------------------------------------------------------------


# Import libraries and data

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib
import os
import folium
import json
import geopandas as gpd

In [2]:
#create string for the path 

path = r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\02 Data\Prepared Data'
path1 =r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations'
path_json =r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\bezirke.json'

In [3]:
# define column types
dtype_options = {'15':str}

In [4]:
# Import data

df = pd.read_csv(os.path.join(path,'3.0 AirBnB_categorical columns.csv'), index_col = 0)

C:\Users\kilia\AppData\Local\Temp\ipykernel_388568\1339579203.py:3: DtypeWarning: Columns (15) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(os.path.join(path,'3.0 AirBnB_categorical columns.csv'), index_col = 0)


In [5]:
%matplotlib inline

In [6]:
# Display all columns 

pd.set_option('display.max_columns', None)

# General Data checking

In [7]:
df.head(3)

Review ID Review_Date  Reviewer ID  \
index                                       
0       58660447  2016-01-03     14876562   
2       58663795  2016-01-03     49367757   
3       59003619  2016-01-05     46694292   

                                          Rating_Comment  Listing ID  \
index                                                                  
0      Very nice, clean appartement! Josh was really ...    10002699   
2      Aki is really nice and friendly. We had an ama...    10006647   
3      Aki is a very nice dude with a clean place in ...    10006647   

                         Listing Name   Host ID  Host Since  \
index                                                         
0      Trendy and peaceful Kreuzkölln  44696672  2015-09-20   
2         Very central and very quite  40791092  2015-08-07   
3         Very central and very quite  40791092  2015-08-07   

       Host Response Time  Host Response Rate  Is Superhost Neighborhood  \
index                                                                      
0                     NaN                 NaN         False     Neukölln   
2      within a few hours               100.0         False        Mitte   
3      within a few hours               100.0         False        Mitte   

      Neighborhood Group    City Postal Code  Country  Latitude  Longitude  \
index                                                                        
0               Neukölln  Berlin     12047.0  Germany  52.49234   13.42994   
2                  Mitte  Berlin     10178.0  Germany  52.52134   13.41866   
3                  Mitte  Berlin     10178.0  Germany  52.52134   13.41866   

      Property Type        Room Type  Accomodates  Bathrooms  Bedrooms  Beds  \
index                                                                          
0         Apartment  Entire home/apt            4        1.0       2.0   2.0   
2         Apartment     Private room            2        1.0       1.0   1.0   
3         Apartment     Private room            2        1.0       1.0   1.0   

       Price  Guests Included  Min Nights  Reviews First Review Last Review  \
index                                                                         
0       60.0                1           1        1   2016-01-03  2016-01-03   
2       35.0                1           1       20   2016-01-03  2017-02-12   
3       35.0                1           1       20   2016-01-03  2017-02-12   

       Overall Rating  Accuracy Rating  Cleanliness Rating  Checkin Rating  \
index                                                                        
0               100.0              8.0                10.0             6.0   
2                92.0              9.0                 8.0             9.0   
3                92.0              9.0                 8.0             9.0   

       Communication Rating  Location Rating  Value Rating  Instant Bookable  \
index                                                                          
0                      10.0             10.0          10.0             False   
2                      10.0             10.0           9.0             False   
3                      10.0             10.0           9.0             False   

      Price category Rating Category    Accomodation Size  
index                                                      
0       Middle price     Good Rating  Couple Accomodation  
2       Middle price     Good Rating  Single Accomodation  
3       Middle price     Good Rating  Single Accomodation

In [8]:
# Reset index colun 

df = df.reset_index(drop=True)


In [9]:
df['Neighborhood Group'].value_counts()

Mitte                       116945
Friedrichshain-Kreuzberg    105971
Pankow                       80208
Neukölln                     50860
Charlottenburg-Wilm.         32474
Tempelhof - Schöneberg       29591
Lichtenberg                  11234
Treptow - Köpenick            8970
Steglitz - Zehlendorf         6618
Reinickendorf                 5514
Marzahn - Hellersdorf         2707
Spandau                       1713
Name: Neighborhood Group, dtype: int64

In [10]:
df.shape

(452805, 41)

# Subsetting/Cleaning

In [11]:
# Create Subset with column needed for geo analysis 

geo_subset = df[df['Price'] < 500][['Price','Accomodates', 'Beds', 'Overall Rating',
                'Cleanliness Rating', 'Location Rating', 'Value Rating', 'Neighborhood Group', 'Neighborhood']] 

# I know there are extreme values in the price column so I filter for price under 500, only 792 values filtered out 
# As I know from previous data cleaning all other columns should be ok for analysis

In [12]:
geo_subset.head(20)

Price  Accomodates  Beds  Overall Rating  Cleanliness Rating  \
0    60.0            4   2.0           100.0                10.0   
1    35.0            2   1.0            92.0                 8.0   
2    35.0            2   1.0            92.0                 8.0   
3    35.0            2   1.0            92.0                 8.0   
4    35.0            2   1.0            92.0                 8.0   
5    35.0            2   1.0            92.0                 8.0   
6    35.0            2   1.0            92.0                 8.0   
7    35.0            2   1.0            92.0                 8.0   
8    35.0            2   1.0            92.0                 8.0   
9    35.0            2   1.0            92.0                 8.0   
10   35.0            2   1.0            92.0                 8.0   
11   35.0            2   1.0            92.0                 8.0   
12   35.0            2   1.0            92.0                 8.0   
13   35.0            2   1.0            92.0                 8.0   
14   35.0            2   1.0            92.0                 8.0   
15   35.0            2   1.0            92.0                 8.0   
16   35.0            2   1.0            92.0                 8.0   
17   35.0            2   1.0            92.0                 8.0   
18   35.0            2   1.0            92.0                 8.0   
19   35.0            2   1.0            92.0                 8.0   

    Location Rating  Value Rating Neighborhood Group Neighborhood  
0              10.0          10.0           Neukölln     Neukölln  
1              10.0           9.0              Mitte        Mitte  
2              10.0           9.0              Mitte        Mitte  
3              10.0           9.0              Mitte        Mitte  
4              10.0           9.0              Mitte        Mitte  
5              10.0           9.0              Mitte        Mitte  
6              10.0           9.0              Mitte        Mitte  
7              10.0           9.0              Mitte        Mitte  
8              10.0           9.0              Mitte        Mitte  
9              10.0           9.0              Mitte        Mitte  
10             10.0           9.0              Mitte        Mitte  
11             10.0           9.0              Mitte        Mitte  
12             10.0           9.0              Mitte        Mitte  
13             10.0           9.0              Mitte        Mitte  
14             10.0           9.0              Mitte        Mitte  
15             10.0           9.0              Mitte        Mitte  
16             10.0           9.0              Mitte        Mitte  
17             10.0           9.0              Mitte        Mitte  
18             10.0           9.0              Mitte        Mitte  
19             10.0           9.0              Mitte        Mitte

In [13]:
geo_subset.shape

(452013, 9)

In [14]:
# Check missing values 

geo_subset.isnull().sum()

Price                   0
Accomodates             0
Beds                   72
Overall Rating        559
Cleanliness Rating    590
Location Rating       615
Value Rating          616
Neighborhood Group      0
Neighborhood            0
dtype: int64

In [15]:
616/(452805/100)

0.13604090060842966

#### that amount of missing data is ok, only 0.13% at the most. 

In [16]:
# Check values for neighborhood groups

geo_subset['Neighborhood Group'].value_counts()

Mitte                       116762
Friedrichshain-Kreuzberg    105669
Pankow                       80015
Neukölln                     50844
Charlottenburg-Wilm.         32388
Tempelhof - Schöneberg       29580
Lichtenberg                  11233
Treptow - Köpenick            8970
Steglitz - Zehlendorf         6618
Reinickendorf                 5514
Marzahn - Hellersdorf         2707
Spandau                       1713
Name: Neighborhood Group, dtype: int64

In [17]:
# Check duplicates

dups = geo_subset.duplicated()

In [18]:
dups.shape

# no dups

(452013,)

In [19]:
# Edit neighborhood names to match with encoding of german ö in the json file

geo_subset['Neighborhood Group'] = geo_subset['Neighborhood Group'].replace('Treptow - Köpenick', 'Treptow - K\u00c3\u00b6penick')


In [20]:
geo_subset['Neighborhood Group'] = geo_subset['Neighborhood Group'].replace('Neukölln', 'Neuk\u00c3\u00b6lln')

In [21]:
geo_subset['Neighborhood Group'] = geo_subset['Neighborhood Group'].replace('Tempelhof - Schöneberg', 'Tempelhof - Sch\u00c3\u00b6neberg')

In [22]:
geo_subset['Neighborhood Group'].value_counts()

Mitte                       116762
Friedrichshain-Kreuzberg    105669
Pankow                       80015
NeukÃ¶lln                    50844
Charlottenburg-Wilm.         32388
Tempelhof - SchÃ¶neberg      29580
Lichtenberg                  11233
Treptow - KÃ¶penick           8970
Steglitz - Zehlendorf         6618
Reinickendorf                 5514
Marzahn - Hellersdorf         2707
Spandau                       1713
Name: Neighborhood Group, dtype: int64

# Aggregating averages

In [23]:
columns_for_mean = ['Price','Accomodates', 'Beds', 'Overall Rating',
                'Cleanliness Rating', 'Location Rating', 'Value Rating']

In [24]:
# Aggregate avg values for each neighborhood

avg_geo_subset = geo_subset.groupby('Neighborhood Group')[columns_for_mean].mean()
avg_geo_subset

Price  Accomodates      Beds  Overall Rating  \
Neighborhood Group                                                           
Charlottenburg-Wilm.      64.730919     3.085248  1.864487       93.991715   
Friedrichshain-Kreuzberg  64.811288     2.980117  1.842412       94.775653   
Lichtenberg               51.529155     3.092673  2.037664       94.558509   
Marzahn - Hellersdorf     51.211304     3.121906  2.421656       95.591111   
Mitte                     78.706591     3.385673  2.076204       93.936859   
NeukÃ¶lln                 56.054166     2.823873  1.672831       94.532722   
Pankow                    69.035468     3.061001  1.887146       94.925021   
Reinickendorf             41.299057     2.951215  1.956656       94.845273   
Spandau                   47.798015     2.936953  2.048852       95.683995   
Steglitz - Zehlendorf     52.246147     2.742218  1.785887       96.086766   
Tempelhof - SchÃ¶neberg   67.152265     3.162508  1.933333       95.182040   
Treptow - KÃ¶penick       49.402453     2.864883  1.918042       95.564873   

                          Cleanliness Rating  Location Rating  Value Rating  
Neighborhood Group                                                           
Charlottenburg-Wilm.                9.455743         9.599283      9.405634  
Friedrichshain-Kreuzberg            9.472311         9.770669      9.436311  
Lichtenberg                         9.456564         9.189368      9.491125  
Marzahn - Hellersdorf               9.764815         8.835185      9.591852  
Mitte                               9.490124         9.664103      9.340998  
NeukÃ¶lln                           9.387828         9.471362      9.412426  
Pankow                              9.595877         9.718968      9.464226  
Reinickendorf                       9.523818         9.160364      9.556182  
Spandau                             9.497079         9.157710      9.557827  
Steglitz - Zehlendorf               9.720927         9.578740      9.555118  
Tempelhof - SchÃ¶neberg             9.573237         9.668235      9.512153  
Treptow - KÃ¶penick                 9.568174         9.290820      9.651887

In [25]:
avg_geo_subset = avg_geo_subset.reset_index()
avg_geo_subset

Neighborhood Group      Price  Accomodates      Beds  \
0       Charlottenburg-Wilm.  64.730919     3.085248  1.864487   
1   Friedrichshain-Kreuzberg  64.811288     2.980117  1.842412   
2                Lichtenberg  51.529155     3.092673  2.037664   
3      Marzahn - Hellersdorf  51.211304     3.121906  2.421656   
4                      Mitte  78.706591     3.385673  2.076204   
5                  NeukÃ¶lln  56.054166     2.823873  1.672831   
6                     Pankow  69.035468     3.061001  1.887146   
7              Reinickendorf  41.299057     2.951215  1.956656   
8                    Spandau  47.798015     2.936953  2.048852   
9      Steglitz - Zehlendorf  52.246147     2.742218  1.785887   
10   Tempelhof - SchÃ¶neberg  67.152265     3.162508  1.933333   
11       Treptow - KÃ¶penick  49.402453     2.864883  1.918042   

    Overall Rating  Cleanliness Rating  Location Rating  Value Rating  
0        93.991715            9.455743         9.599283      9.405634  
1        94.775653            9.472311         9.770669      9.436311  
2        94.558509            9.456564         9.189368      9.491125  
3        95.591111            9.764815         8.835185      9.591852  
4        93.936859            9.490124         9.664103      9.340998  
5        94.532722            9.387828         9.471362      9.412426  
6        94.925021            9.595877         9.718968      9.464226  
7        94.845273            9.523818         9.160364      9.556182  
8        95.683995            9.497079         9.157710      9.557827  
9        96.086766            9.720927         9.578740      9.555118  
10       95.182040            9.573237         9.668235      9.512153  
11       95.564873            9.568174         9.290820      9.651887

# Plot choropleths

In [26]:
# Create data subset with variables to plot 

price_plot = avg_geo_subset[['Neighborhood Group','Price']]
price_plot.head(10)

Neighborhood Group      Price
0      Charlottenburg-Wilm.  64.730919
1  Friedrichshain-Kreuzberg  64.811288
2               Lichtenberg  51.529155
3     Marzahn - Hellersdorf  51.211304
4                     Mitte  78.706591
5                 NeukÃ¶lln  56.054166
6                    Pankow  69.035468
7             Reinickendorf  41.299057
8                   Spandau  47.798015
9     Steglitz - Zehlendorf  52.246147

In [27]:
# Setup a folium map at a high-level zoom
map = folium.Map(location = [52.35,13.3], zoom_start = 9.3)

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = path_json, 
    data = price_plot,
    columns = ['Neighborhood Group', 'Price'],
    key_on = 'properties.neighbourhood_group', # this part is very important - check your json file to see where the KEY is located
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Price").add_to(map)
folium.LayerControl().add_to(map)

map

In [28]:
map.save(r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations\Price per Neighborhood.html')

In [29]:
# Create Subset for Cholopleth

cleanliness_plot = avg_geo_subset[['Neighborhood Group','Cleanliness Rating']]
cleanliness_plot.head(12)

Neighborhood Group  Cleanliness Rating
0       Charlottenburg-Wilm.            9.455743
1   Friedrichshain-Kreuzberg            9.472311
2                Lichtenberg            9.456564
3      Marzahn - Hellersdorf            9.764815
4                      Mitte            9.490124
5                  NeukÃ¶lln            9.387828
6                     Pankow            9.595877
7              Reinickendorf            9.523818
8                    Spandau            9.497079
9      Steglitz - Zehlendorf            9.720927
10   Tempelhof - SchÃ¶neberg            9.573237
11       Treptow - KÃ¶penick            9.568174

In [30]:
# Setup a folium map at a high-level zoom
map = folium.Map(location = [52.5,13.3], zoom_start = 10)

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = path_json, 
    data = cleanliness_plot,
    columns = ['Neighborhood Group', 'Cleanliness Rating'],
    key_on = 'properties.neighbourhood_group', # this part is very important - check your json file to see where the KEY is located
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Price").add_to(map)
folium.LayerControl().add_to(map)

map

In [31]:
map.save(r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations\Cleanliness Rating.html')

In [32]:
# Create Subset for Cholopleth

Rating_plot = avg_geo_subset[['Neighborhood Group','Overall Rating']]
Rating_plot.head(12)

Neighborhood Group  Overall Rating
0       Charlottenburg-Wilm.       93.991715
1   Friedrichshain-Kreuzberg       94.775653
2                Lichtenberg       94.558509
3      Marzahn - Hellersdorf       95.591111
4                      Mitte       93.936859
5                  NeukÃ¶lln       94.532722
6                     Pankow       94.925021
7              Reinickendorf       94.845273
8                    Spandau       95.683995
9      Steglitz - Zehlendorf       96.086766
10   Tempelhof - SchÃ¶neberg       95.182040
11       Treptow - KÃ¶penick       95.564873

In [33]:
# Setup a folium map at a high-level zoom
map = folium.Map(location = [52.5,13.3], zoom_start = 10)

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = path_json, 
    data = Rating_plot,
    columns = ['Neighborhood Group', 'Overall Rating'],
    key_on = 'properties.neighbourhood_group', # this part is very important - check your json file to see where the KEY is located
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Price").add_to(map)
folium.LayerControl().add_to(map)

map

In [34]:
map.save(r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations\Overall Rating.html')

In [35]:
# Create Subset for Cholopleth

Value_Rating_plot = avg_geo_subset[['Neighborhood Group','Value Rating']]
Value_Rating_plot.head(12)

Neighborhood Group  Value Rating
0       Charlottenburg-Wilm.      9.405634
1   Friedrichshain-Kreuzberg      9.436311
2                Lichtenberg      9.491125
3      Marzahn - Hellersdorf      9.591852
4                      Mitte      9.340998
5                  NeukÃ¶lln      9.412426
6                     Pankow      9.464226
7              Reinickendorf      9.556182
8                    Spandau      9.557827
9      Steglitz - Zehlendorf      9.555118
10   Tempelhof - SchÃ¶neberg      9.512153
11       Treptow - KÃ¶penick      9.651887

In [36]:
# Setup a folium map at a high-level zoom
map = folium.Map(location = [52.5,13.3], zoom_start = 10)

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = path_json, 
    data = Value_Rating_plot,
    columns = ['Neighborhood Group', 'Value Rating'],
    key_on = 'properties.neighbourhood_group', # this part is very important - check your json file to see where the KEY is located
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Price").add_to(map)
folium.LayerControl().add_to(map)

map


In [37]:
map.save(r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations\Value Rating.html')

In [38]:
# Create Subset for Cholopleth

Accomodates_plot = avg_geo_subset[['Neighborhood Group','Accomodates']]
Accomodates_plot.head(12)

Neighborhood Group  Accomodates
0       Charlottenburg-Wilm.     3.085248
1   Friedrichshain-Kreuzberg     2.980117
2                Lichtenberg     3.092673
3      Marzahn - Hellersdorf     3.121906
4                      Mitte     3.385673
5                  NeukÃ¶lln     2.823873
6                     Pankow     3.061001
7              Reinickendorf     2.951215
8                    Spandau     2.936953
9      Steglitz - Zehlendorf     2.742218
10   Tempelhof - SchÃ¶neberg     3.162508
11       Treptow - KÃ¶penick     2.864883

In [39]:
# Setup a folium map at a high-level zoom
map = folium.Map(location = [52.5,13.3], zoom_start = 10)

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = path_json, 
    data = Accomodates_plot,
    columns = ['Neighborhood Group', 'Accomodates'],
    key_on = 'properties.neighbourhood_group', # this part is very important - check your json file to see where the KEY is located
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Price").add_to(map)
folium.LayerControl().add_to(map)

map

In [40]:
map.save(r'C:\Users\kilia\OneDrive\CareerFoundry\Projects\Data Immersion Course\Achievement 6\Berlin_AirBnB Analysis\04 Analysis\Visualizations\Accomodates.html')

# Discuss Results 

### Questions answered with the plots
### Have some neighborhoods far better ratings than others?

#### The average ratings are not very far from each other. But it is noticable that the district Mitte has the worst overall ratings.

### Which neighborhood is most pricey and least pricey?

#### As I expected the districts in the city center are more pricey. The most expensive neighborhood is Mitte and the least expensive neighborhood is  Reinickendorf. 

### Are there certain neighborhoods where the cleanliness rating is unusually low?

#### The worst cleanliness rating has Berlin Neukölln, but it isn't off that much. The best cleanliness rating has Marzahn - Hellersdorf and Steglitz - Zehlendorf.




### Is the analysis leading to new research questions? 

#### Why the prices in Pankow and Tempelhof - Schöneberg are relatively high in comparison? 
#### Whats special about Steglitz - Zehlendorf? It has low price but the best rating. 